## Exploring stability of persistent homology

We will look at the behaviour (as it is implied by the stability theorem) of persistent homology.

We will be using Julia packages `LinearAlgebra`, `Plots`, `PersistenceDiagrams`, and, of course, `Ripserer`. Make sure you have these preinstalled.

In [1]:
# Let's load the packages.
using LinearAlgebra, Plots, Ripserer, PersistenceDiagrams

In [ ]:
# a function which generates a sample point cloud representing 
# a circle of radius r with center at the point (p, q)
function circle(r = 1, center = (0,0), rel_noise = 0.1, num = 100)
    points = NTuple{2,Float64}[]
    num_points = 0
    while num_points <= num
        # a random point in the square [-1, 1]x[-1, 1]
        point = 2*(1+rel_noise)*rand(2, 1) .- (1+rel_noise)
        # check if this point is in the annulus with radii 1 +/- rel_noise
        if 1-rel_noise <= norm(point) <= 1+rel_noise
            # and add it
            push!(points, Tuple(r*point + collect(center)))
            num_points += 1
        end
    end
    return points
end

In [ ]:
# first simple example
theme(:dark) # optional
# a 10-second animation of a 'noisy' circle 
# We create an animation object ...
anim1 = @animate for i in 1:100
    # generate the circle
    points = circle(1, Tuple(0.2*rand(2, 1) .- 0.1))
    # compute persistent homology with ripserer
    result = ripserer(points)

    plt_pts = scatter(
        points;
        legend=false,
        aspect_ratio=1,
        xlim=(-1.3, 1.3),
        ylim=(-1.3, 1.3),
        title="Data",
    )
    plt_diag = plot(result; infinity=2)

    plot(plt_pts, plt_diag; size=(800, 400))
end
# ... and display it as an animated gif.
gif(anim1, fps = 15)

In [ ]:
# second example
# a circle with changing radius
anim2 = @animate for i in 1:100
    # generate the circle
    r = 0.9*cos(pi*i/100)^2+0.1
    points = circle(r, Tuple(0.2*rand(2, 1) .- 0.1), 0.1/r)
    # compute persistent homology with ripserer
    result = ripserer(points)

    plt_pts = scatter(
        points;
        legend=false,
        aspect_ratio=1,
        xlim=(-1.3, 1.3),
        ylim=(-1.3, 1.3),
        title="Data",
    )
    plt_diag = plot(result; infinity=2)

    plot(plt_pts, plt_diag; size=(800, 400))
end
gif(anim2, fps = 15)

In [ ]:
# Let's create an animation object where two noisy circles start up disjoint, then merge 
# and separate again.
# We also plot the H1 generators which are 'persistent enough'. ('persistent enough' depends on the ripserer cutoff kwarg.)
anim3 = @animate for i in 1:100
    # generate the first circle
    points = circle(1, (1.5-i/33.3, 0))
    # and append the second circle to it
    append!(points, circle(1, (-1.5+i/33.3, 0)))
    # compute persistent homology with ripserer 
    # (This actually coputes cohomology. Recunstructed homology representatives 'look nicer' this way.)
    # (Try this with different cuttoffs.)
    result = ripserer(points; cutoff = 0.1, reps = true)

    plt_pts = scatter(
        points;
        legend=false,
        aspect_ratio=1,
        xlim=(-3.2, 3.2),
        ylim=(-1.2, 1.2),
        title="Data",
    )
    # let's also plot the H1 generators (those are the 'reconstructed cycles')
    for gen in result[2]
        plot!(reconstruct_cycle(result[2].filtration, gen), points; linewidth = 4)
    end
    plt_diag = plot(result; infinity=2)

    plot(plt_pts, plt_diag; size=(800, 400))
end
gif(anim3, fps = 15)

In [ ]:
# preparation for a 3D example
# 
# a function to generate a point cloud of points on a torus
function torus(R = 2, r = 1, rel_noise = 0.1, num = 1000)
    points = NTuple{3,Float64}[]
    num_points = 0
    while num_points <= num
        # a random point in the box [-R-r, R+r]x[-R-r, R+r]x[-r, r]
        point = 2*[(R+r)*(1+rel_noise); (R+r)*(1+rel_noise); r*(1+rel_noise)].*rand(3, 1) .- [(R+r)*(1+rel_noise); (R+r)*(1+rel_noise); r*(1+rel_noise)]
        # check if this point is in the thickened torus
        if r*(1-rel_noise) <= norm([R+norm(point[1:2]); point[3]]) <= r*(1+rel_noise) || r*(1-rel_noise) <= norm([R-norm(point[1:2]); point[3]]) <= r*(1+rel_noise)
            # and add it
            push!(points, Tuple(point))
            num_points += 1
        end
    end
    return points
end

In [ ]:
# let's see how it works
points = torus()
plt_torus = scatter(points; label="", lims = (-3.3, 3.3), markersize = 1)
result = ripserer(points; dim_max = 2, threshold = 2.2, reps = true)
# let's also plot the two most persistent H1 generators as reconstructed cycles
# we reconstruct the H1 cycles at the midpoint of the persistence interval
for gen in result[2][(end-1):end]
    plot!(reconstruct_cycle(result[2].filtration, gen, 0.5*(death(gen)-birth(gen))), points; linewidth = 2, label = "H1 rep")
end
plt_diag = plot(result)

plot(plt_torus, plt_diag; size=(800, 400))

The example below is an attempt to continously change a torus to a sphere. Note that the torus with "big" radius $R$ and "small" radius $r$ can be given implicitly as 
$$
    (R - \sqrt{x^2+y^2})^2 + z^2 = r^2.
$$
(This equation is essentially used to generate the point cloud in the function `torus` above.) Also note that the case $R = 0$ gives the equation of a sphere with radius $r$. 

So slowly decreasing $R$ to $0$ should give a continous deformation from a torus to a sphere. Observe that there are two '3D holes' at some instant during this deformation (if $r > R > 0$ holds). Their appearance should be clearly (albeit also only quickly) visible on the persistence diagram.

In [ ]:
# Let's create an animation of a torus 'becoming' a sphere.
#
# This example does take a while to compute. You can play with num_frames = 150 and threshold = 1.5 (ripserer's kwarg) to 
# speed this up (or slow it down).
num_frames = 150
anim4 = @animate for i in 1:num_frames
    # generate the torus/sphere
    points = torus(2-2*abs(1-2*i/num_frames), 1+1.5*abs(1-2*i/num_frames), 0.05, 1200)
    result = ripserer(points; dim_max = 2, threshold = 1.5, cutoff = 0.2)

    plt_pts = scatter(
        points;
        legend=false,
        aspect_ratio=1,
        lims = (-3.2, 3.2),
        title="Data",
        markersize = 1
    )
    plt_diag = plot(result; infinity = 3)

    plot(plt_pts, plt_diag; size=(800, 400))
end
gif(anim4; fps = num_frames/8)

## Tricking Ripserer into usual homology computation

We can use `Ripserer` to compute usual homology groups, too. We simply give it a filtration with a single level as an input.

In [ ]:
# Start by defining a known function (again).
# Compute the boundary of a simplex sx and represent it as a list of maximal simplices, 
# i.e., just determine the codimenstion 1 faces of sx. 
# E.g. for sx = (1, 2, 3) we get [(1, 2), (1, 3), (2, 3)].
function simplex_boundary(sx)
    # determine the codimension 1 simplices in the boundary of the simplex sx
    # 'remove' one entry of a tuple at each specific index by splicing the corresponding subtuples
    cd1faces = ([(sx[1:k-1]..., sx[k+1:end]...) for k in eachindex(sx)])
    return cd1faces
end

In [ ]:
# a 14-sphere presented as the boundary of a 15-simplex
K = simplex_boundary(Tuple(1:16))
# the corresponding custom filtration for ripserer
Kfilt = Custom([simplex => 0 for simplex in K])
# and its (persistent) homology computation
# (This returns the wrong result with 'alg = :homology'. A bug in ripserer?)
ripserer(Kfilt; dim_max = 14, alg = :involuted)